In [1]:
import os
import pandas as pd
import numpy as np
import sys
sys.path.append('../../Scripts')
from preprocess_daily import DailyPreprocessor
from generate_signals import SignalGenerator

In [2]:
self = DailyPreprocessor()
self.load_data()
self.make_match1()
self.make_match2()
self.make_match3()
self.make_match4()
self.make_match5()
self.make_match6()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
1-5. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.


In [3]:
self.match6

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0         175         1         A        8        남        북       179   
1         175         1         B        4        북        남       001   
2         175         2         A        7        북        동       001   
3         175         2         B        3        남        서       179   
4         175         3         A        6        동        서       090   
..        ...       ...       ...      ...      ...      ...       ...   
103       210         2         B        2        서        동       270   
104       210         3         A        7        북        동       000   
105       210         3         B        4        북        남       000   
106       210         4         A        8        남        북       180   
107       210         4         B        3        남        서       180   

    out_angle    inc_edge_id   out_edge_id node_id turn_type  
0         000  -571542797_02  571500487_01      i0  straight  
1         180  -571500487_01  571542797_02      i0  straight  
2         090  -571500487_01  571545870_01      i0      left  
3         270  -571542797_02  571510153_01      i0      left  
4         270   571545870_02  571510153_01      i0  straight  
..        ...            ...           ...     ...       ...  
103       090            NaN           NaN     u60  straight  
104       090            NaN           NaN     u60      left  
105       180            NaN           NaN     u60  straight  
106       000            NaN           NaN     u60  straight  
107       270            NaN           NaN     u60      left  

[108 rows x 12 columns]

In [4]:
self.match7 = self.match6.copy()
self.match7 = self.match7[['inter_no', 'node_id', 'move_no', 'inc_angle', 'out_angle', 'inc_dire', 'out_dire', 'inc_edge_id', 'out_edge_id']]

# (1) 각 교차로별 방향 목록 : pdires (possible directions)
p2dires = {} # parent_id to directions
for parent_id in self.parent_ids:
    dires = self.match7[self.match7.node_id == parent_id][['inc_dire','out_dire']].values.flatten()
    dires = {dire for dire in dires if type(dire)==str}
    p2dires[parent_id] = dires

# (2) 각 (교차로, 진입방향) 별 진입id 목록 : inc2id (incoming direction to incoming edge_id)
inc2id = {}
for parent_id in self.parent_ids:
    for inc_dire in p2dires[parent_id]:
        df = self.match7[(self.match7.node_id==parent_id) & (self.match7.inc_dire==inc_dire)]
        inc2id[(parent_id, inc_dire)] = df.inc_edge_id.iloc[0]

# (3) 각 (교차로, 진출방향) 별 진출id 목록 : out2id (outgoing direction to outgoing edge_id)
out2id = {}
for parent_id in self.parent_ids:
    for out_dire in p2dires[parent_id]:
        df = self.match7[(self.match7.node_id==parent_id) & (self.match7.out_dire==out_dire)]
        out2id[(parent_id, out_dire)] = df.out_edge_id.iloc[0]

# (4) 각 parent_id별 이동류번호 목록
p2move = dict() # parent id to a list of aligned movement numbers
for parent_id in self.parent_ids:
    pnema = self.nema[self.nema.inc_dire.isin(p2dires[parent_id]) & self.nema.out_dire.isin(p2dires[parent_id])]
    p2move[parent_id] = list(pnema.move_no)

# (5) 방위별 방향벡터
dire2vec = dict() # direction to unit vector
theta = np.pi/2
for dire in self.dires:
    dire2vec[dire] = np.array([np.cos(theta), np.sin(theta)])
    theta -= np.pi/4

# (6) 각 parent_id별 : 각 이동류별 진입/진출 엣지 id
p2move2inc_edge_id = dict() # parent id to move2inc_edge_id
p2move2out_edge_id = dict() # parent id to move2out_edge_id
for parent_id in self.parent_ids:
    move2inc_edge_id = dict() # plain movement to incoming edge id
    move2out_edge_id = dict() # plain movement to outgoing edge id
    for move_no in range(1,17):
        row = self.nema[self.nema.move_no==move_no].iloc[0]
        inc_dire = row.inc_dire
        out_dire = row.out_dire
        inc_vec_true = dire2vec[inc_dire]
        out_vec_true = dire2vec[out_dire]

        node = self.net.getNode(parent_id)
        # 교차로의 모든 (from / to) edges
        inc_edges = [edge for edge in node.getIncoming() if edge.getFunction() == ''] # incoming edges
        out_edges = [edge for edge in node.getOutgoing() if edge.getFunction() == ''] # outgoing edges
        # 교차로의 모든 (from / to) unit vector
        inc_vecs = []
        for inc_edge in inc_edges:
            start = inc_edge.getShape()[-1]
            end = inc_edge.getShape()[-2]
            inc_vec = np.array(end) - np.array(start)
            inc_vec = inc_vec / (inc_vec ** 2).sum() ** 0.5
            inc_vecs.append(inc_vec)
        out_vecs = []
        for out_edge in out_edges:
            start = out_edge.getShape()[0]
            end = out_edge.getShape()[1]
            out_vec = np.array(end) - np.array(start)
            out_vec = out_vec / (out_vec ** 2).sum() ** 0.5
            out_vecs.append(out_vec)
        # 매칭 엣지 반환
        inc_index = np.array([np.dot(inc_vec, inc_vec_true) for inc_vec in inc_vecs]).argmax()
        out_index = np.array([np.dot(out_vec, out_vec_true) for out_vec in out_vecs]).argmax()
        inc_edge_id = inc_edges[inc_index].getID()
        out_edge_id = out_edges[out_index].getID()
        move2inc_edge_id[move_no] = inc_edge_id
        move2out_edge_id[move_no] = out_edge_id
    p2move2inc_edge_id[parent_id] = move2inc_edge_id
    p2move2out_edge_id[parent_id] = move2out_edge_id

# (7) 각 이동류별 진입/진출 방위
m2inc_dire = dict()
m2out_dire = dict()
for move_no in range(1,17):
    row = self.nema[self.nema.move_no==move_no].iloc[0]
    m2inc_dire[move_no] = row.inc_dire
    m2out_dire[move_no] = row.out_dire

# (8) 가능한 모든 이동류에 대하여 진입id, 진출id 배정 : matching
self.matching = []
for parent_id in self.parent_ids:
    inter_no = self.node2inter[parent_id]
    # 좌회전과 직진(1 ~ 16)
    for move_no in range(1,17):
        inc_dire = m2inc_dire[move_no]
        out_dire = m2out_dire[move_no]
        if move_no in p2move[parent_id]:
            inc_edge_id = inc2id[(parent_id, inc_dire)]
            out_edge_id = out2id[(parent_id, out_dire)]
        else:
            inc_edge_id = p2move2inc_edge_id[parent_id][move_no]
            out_edge_id = p2move2out_edge_id[parent_id][move_no]
        if (inc_edge_id, out_edge_id) in self.n2io2turn[parent_id]:
            turn_type = self.n2io2turn[parent_id][inc_edge_id, out_edge_id]
        else:
            turn_type = 'left' if move_no%2 else 'straight'
        new_row = pd.DataFrame({'inter_no':[inter_no], 'node_id':[parent_id], 'move_no':[move_no],
                                'inc_dire':[inc_dire], 'out_dire':[out_dire],
                                'inc_edge_id':[inc_edge_id], 'out_edge_id':[out_edge_id],
                                'turn_type': turn_type})
        self.matching.append(new_row)
child_matching = self.match7[self.match7.node_id.isin(self.child_ids)]
child_matching = child_matching.drop(columns=['inc_angle', 'out_angle'])
self.matching = pd.concat(self.matching)
self.matching = self.matching.dropna(subset=['inc_edge_id', 'out_edge_id'])\
                .sort_values(by=['inter_no', 'node_id', 'move_no']).reset_index(drop=True)
self.matching['move_no'] = self.matching['move_no'].astype(int)
self.matching

inter_no node_id  move_no inc_dire out_dire       inc_edge_id  \
0         175      i0        1        동        남      571545870_02   
1         175      i0        2        서        동      571510153_02   
2         175      i0        3        남        서     -571542797_02   
3         175      i0        4        북        남     -571500487_01   
4         175      i0        5        서        북      571510153_02   
..        ...     ...      ...      ...      ...               ...   
123       210      i6       12       북서       남동   571500535_02.18   
124       210      i6       13       남서       북서      571500585_02   
125       210      i6       14       북동       남서  571511538_02.121   
126       210      i6       15       북서       북동   571500535_02.18   
127       210      i6       16       남동       북서     -571542115_01   

      out_edge_id turn_type  
0    571542797_02      left  
1    571545870_01  straight  
2    571510153_01      left  
3    571542797_02  straight  
4    571500487_01      left  
..            ...       ...  
123  571542115_01  straight  
124  571500535_01      left  
125  571500585_01  straight  
126  571511538_01      left  
127  571500535_01  straight  

[128 rows x 8 columns]

In [6]:
self.n2io2turn['i0']

{('-571542797_02', '571500487_01'): 'straight',
 ('-571500487_01', '571542797_02'): 'straight',
 ('-571500487_01', '571545870_01'): 'left',
 ('-571542797_02', '571510153_01'): 'left',
 ('571545870_02', '571510153_01'): 'straight',
 ('571545870_02', '571542797_02'): 'left',
 ('571510153_02', '571500487_01'): 'left',
 ('571510153_02', '571545870_01'): 'straight'}

In [62]:
# display(self.match1.head())
# display(self.match2.head())
# display(self.match3.head())
# display(self.match4.head())
display(self.match5.head())
display(self.match6.head())
display(self.matching.head())

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0       175         1         A        8        남        북       179   
1       175         1         B        4        북        남       001   
2       175         2         A        7        북        동       001   
3       175         2         B        3        남        서       179   
4       175         3         A        6        동        서       090   

  out_angle    inc_edge_id   out_edge_id node_id turn_type  
0       000  -571542797_02  571500487_01      i0  straight  
1       180  -571500487_01  571542797_02      i0  straight  
2       090  -571500487_01  571545870_01      i0      left  
3       270  -571542797_02  571510153_01      i0      left  
4       270   571545870_02  571510153_01      i0  straight

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0       175         1         A        8        남        북       179   
1       175         1         B        4        북        남       001   
2       175         2         A        7        북        동       001   
3       175         2         B        3        남        서       179   
4       175         3         A        6        동        서       090   

  out_angle    inc_edge_id   out_edge_id node_id turn_type  
0       000  -571542797_02  571500487_01      i0  straight  
1       180  -571500487_01  571542797_02      i0  straight  
2       090  -571500487_01  571545870_01      i0      left  
3       270  -571542797_02  571510153_01      i0      left  
4       270   571545870_02  571510153_01      i0  straight

inter_no  move_no inc_dire out_dire    inc_edge_id   out_edge_id node_id
0       175        1        동        남   571545870_02  571542797_02      i0
1       175        2        서        동   571510153_02  571545870_01      i0
2       175        3        남        서  -571542797_02  571510153_01      i0
3       175        4        북        남  -571500487_01  571542797_02      i0
4       175        5        서        북   571510153_02  571500487_01      i0